In [2]:
import json
import requests
import pandas as pd
import datetime

In [102]:
url = "https://data.wprdc.org/api/3/action/datastore_search_sql"
sql = "?sql=" + \
    "SELECT _id, zone, start,\"end\", meter_transactions, meter_payments, mobile_transactions, mobile_payments " + \
    "FROM \"1ad5394f-d158-46c1-9af7-90a9ef4e0ce1\" " + \
    "WHERE (start>=\'2018-01-01\' AND start < \'2019-01-01\') AND (zone LIKE \'%Oakland%\') " + \
    "ORDER BY start, zone " + \
    "LIMIT 50000 "
#NOTE: for some reason, you have to have it as \"end\" instead of just end in the SELECT query.....keyword issue perhaps?

new_url = url + sql
print("Querying url: \t ", new_url, "\n\n")

Querying url: 	  https://data.wprdc.org/api/3/action/datastore_search_sql?sql=SELECT _id, zone, start,"end", meter_transactions, meter_payments, mobile_transactions, mobile_payments FROM "1ad5394f-d158-46c1-9af7-90a9ef4e0ce1" WHERE (start>='2018-01-01' AND start < '2019-01-01') AND (zone LIKE '%Oakland%') ORDER BY start, zone LIMIT 50000  




In [103]:
response = requests.request("GET", new_url)
json_response = response.json()
bucket_list = json_response['result']['records']
bucket_list

[{'mobile_transactions': 1,
  'end': '2018-01-01T08:00:00',
  'zone': '409 - Oakland 3',
  'meter_transactions': 0,
  'start': '2018-01-01T07:50:00',
  'mobile_payments': 7.5,
  '_id': 19,
  'meter_payments': 0.0},
 {'mobile_transactions': 2,
  'end': '2018-01-01T08:50:00',
  'zone': '407 - Oakland 1',
  'meter_transactions': 0,
  'start': '2018-01-01T08:40:00',
  'mobile_payments': 12.0,
  '_id': 39,
  'meter_payments': 0.0},
 {'mobile_transactions': 1,
  'end': '2018-01-01T10:40:00',
  'zone': '410 - Oakland 4',
  'meter_transactions': 0,
  'start': '2018-01-01T10:30:00',
  'mobile_payments': 1.75,
  '_id': 69,
  'meter_payments': 0.0},
 {'mobile_transactions': 1,
  'end': '2018-01-01T11:00:00',
  'zone': '407 - Oakland 1',
  'meter_transactions': 0,
  'start': '2018-01-01T10:50:00',
  'mobile_payments': 5.25,
  '_id': 78,
  'meter_payments': 0.0},
 {'mobile_transactions': 2,
  'end': '2018-01-01T11:00:00',
  'zone': '410 - Oakland 4',
  'meter_transactions': 0,
  'start': '2018-01-0

In [112]:
aggregates_df = pd.DataFrame(bucket_list)
aggregates_df["start"] = pd.to_datetime(aggregates_df["start"])
aggregates_df['start'] = aggregates_df['start'].dt.tz_localize('US/Eastern')
aggregates_df["end"] = pd.to_datetime(aggregates_df["end"])
aggregates_df['end'] = aggregates_df['end'].dt.tz_localize('US/Eastern')

aggregates_df

mobile_transactions                       end             zone  \
0                        1 2018-01-01 08:00:00-05:00  409 - Oakland 3   
1                        2 2018-01-01 08:50:00-05:00  407 - Oakland 1   
2                        1 2018-01-01 10:40:00-05:00  410 - Oakland 4   
3                        1 2018-01-01 11:00:00-05:00  407 - Oakland 1   
4                        2 2018-01-01 11:00:00-05:00  410 - Oakland 4   
...                    ...                       ...              ...   
49995                    5 2018-07-28 16:10:00-04:00  409 - Oakland 3   
49996                    3 2018-07-28 16:10:00-04:00  410 - Oakland 4   
49997                    1 2018-07-28 16:20:00-04:00  407 - Oakland 1   
49998                    2 2018-07-28 16:20:00-04:00  408 - Oakland 2   
49999                    0 2018-07-28 16:20:00-04:00  409 - Oakland 3   

       meter_transactions                     start  mobile_payments     _id  \
0                       0 2018-01-01 07:50:00-05:00             7.50      19   
1                       0 2018-01-01 08:40:00-05:00            12.00      39   
2                       0 2018-01-01 10:30:00-05:00             1.75      69   
3                       0 2018-01-01 10:50:00-05:00             5.25      78   
4                       0 2018-01-01 10:50:00-05:00             5.25      79   
...                   ...                       ...              ...     ...   
49995                   8 2018-07-28 16:00:00-04:00            18.10  479709   
49996                   6 2018-07-28 16:00:00-04:00             4.25  479710   
49997                  11 2018-07-28 16:10:00-04:00             4.50  479738   
49998                   7 2018-07-28 16:10:00-04:00             7.00  479739   
49999                   8 2018-07-28 16:10:00-04:00             0.00  479740   

       meter_payments  
0                0.00  
1                0.00  
2                0.00  
3                0.00  
4                0.00  
...               ...  
49995           27.65  
49996           24.05  
49997           31.45  
49998           19.60  
49999           14.90  

[50000 rows x 8 columns]

In [113]:
# zones = pd.read_csv("zones.csv")
# aggregates_df = pd.merge(aggregates_df, zones, on='zone')

"""
There's an error with that code ^ because there are two dates in the zones.csv file depending on the as_of. This
tends to lead to a doubling in the number of rows (which really isn't that terrible because it gives some extra data,
but for correctness and eventually creating the 'true' free_spaces column, we'll pretend it is terrible). It 
only affects the spaces column, and does so minimally, so I'm going to take the artistic liberty of some hard coding,
though we'll want to algorithmize this in the future.
"""
oakland_zone_info = [
    {
        "zone": "407 - Oakland 1",
        "rate": "3",
        "total spaces": "227"
    },
    {
        "zone": "408 - Oakland 2",
        "rate": "3",
        "total spaces": "301"
    },
    {
        "zone": "409 - Oakland 3",
        "rate": "3",
        "total spaces": "476"
    },
    {
        "zone": "410 - Oakland 4",
        "rate": "3",
        "total spaces": "572"
    },
]

oakland_zone_info_df = pd.DataFrame(oakland_zone_info)
oakland_zone_info_df

zone rate total spaces
0  407 - Oakland 1    3          227
1  408 - Oakland 2    3          301
2  409 - Oakland 3    3          476
3  410 - Oakland 4    3          572

In [117]:
oakland_aggregates_df = pd.merge(aggregates_df, oakland_zone_info_df, on='zone')

#for some weird reason pandas loses the sort on the merge so we have to resort it
oakland_aggregates_df = oakland_aggregates_df.sort_values(by=['start', 'zone'])

oakland_aggregates_df['free spaces'] = oakland_aggregates_df['total spaces']
oakland_aggregates_df

mobile_transactions                       end             zone  \
0                        1 2018-01-01 08:00:00-05:00  409 - Oakland 3   
12202                    2 2018-01-01 08:50:00-05:00  407 - Oakland 1   
24775                    1 2018-01-01 10:40:00-05:00  410 - Oakland 4   
12203                    1 2018-01-01 11:00:00-05:00  407 - Oakland 1   
24776                    2 2018-01-01 11:00:00-05:00  410 - Oakland 4   
...                    ...                       ...              ...   
12200                    5 2018-07-28 16:10:00-04:00  409 - Oakland 3   
37542                    3 2018-07-28 16:10:00-04:00  410 - Oakland 4   
24774                    1 2018-07-28 16:20:00-04:00  407 - Oakland 1   
49999                    2 2018-07-28 16:20:00-04:00  408 - Oakland 2   
12201                    0 2018-07-28 16:20:00-04:00  409 - Oakland 3   

       meter_transactions                     start  mobile_payments     _id  \
0                       0 2018-01-01 07:50:00-05:00             7.50      19   
12202                   0 2018-01-01 08:40:00-05:00            12.00      39   
24775                   0 2018-01-01 10:30:00-05:00             1.75      69   
12203                   0 2018-01-01 10:50:00-05:00             5.25      78   
24776                   0 2018-01-01 10:50:00-05:00             5.25      79   
...                   ...                       ...              ...     ...   
12200                   8 2018-07-28 16:00:00-04:00            18.10  479709   
37542                   6 2018-07-28 16:00:00-04:00             4.25  479710   
24774                  11 2018-07-28 16:10:00-04:00             4.50  479738   
49999                   7 2018-07-28 16:10:00-04:00             7.00  479739   
12201                   8 2018-07-28 16:10:00-04:00             0.00  479740   

       meter_payments rate total spaces free spaces  
0                0.00    3          476         476  
12202            0.00    3          227         227  
24775            0.00    3          572         572  
12203            0.00    3          227         227  
24776            0.00    3          572         572  
...               ...  ...          ...         ...  
12200           27.65    3          476         476  
37542           24.05    3          572         572  
24774           31.45    3          227         227  
49999           19.60    3          301         301  
12201           14.90    3          476         476  

[50000 rows x 11 columns]

In [107]:
#Next steps: load in the individual transaction data for 2018, select out the oakland zones

#iterate through individuals, determine how many hours need to be have a car subtracted (should just be payment/rate)
#decrement 'free spaces' ahead for each bucket that is within that hour
#be sure to use iloc because the row numbers get screwed up on sorting (new_aggregates_df.iloc[1] != new_aggregates_df.loc[1]

#out pops the final dataframe! convert to csv and train on gcp

In [108]:
individual_records_2018 = pd.read_csv("2018--transactions.csv")
individual_records_2018

meter_id                             zone  \
0                    PBP421                  421 - NorthSide   
1                    PBP412               412 - East Liberty   
2                    PBP421                  421 - NorthSide   
3                  PBP403-3                     403 - Uptown   
4                    PBP335  335 - Friendship Cedarville Lot   
...                     ...                              ...   
7740289   341335-18SDNY0002          341 - 18th & Sidney Lot   
7740290   345341-20SDNY0001          345 - 20th & Sidney Lot   
7740291   341334-18SDNY0001          341 - 18th & Sidney Lot   
7740292  344339-18CARSN0001          344 - 18th & Carson Lot   
7740293   345341-20SDNY0001          345 - 20th & Sidney Lot   

        payment_start_utc   payment_end_utc purchase_date_utc  \
0        2018-01-01T05:24  2018-01-01T16:59               NaN   
1        2018-01-01T06:10  2018-01-01T14:59               NaN   
2        2018-01-01T06:28  2018-01-01T16:59               NaN   
3        2018-01-01T06:18  2018-01-01T14:59               NaN   
4        2018-01-01T11:54  2018-01-01T21:54               NaN   
...                   ...               ...               ...   
7740289  2019-01-01T02:48  2019-01-01T03:00  2019-01-01T02:48   
7740290  2019-01-01T02:33  2019-01-01T03:00  2019-01-01T02:33   
7740291  2019-01-01T02:26  2019-01-01T03:00  2019-01-01T02:26   
7740292  2019-01-01T02:36  2019-01-01T03:00  2019-01-01T02:36   
7740293  2019-01-01T02:05  2019-01-01T02:20  2019-01-01T02:05   

            date_recorded_utc  amount payment_type purchase_type  
0        2018-01-01T05:24:04.    4.00       Mobile           New  
1        2018-01-01T06:10:38.    3.00       Mobile           New  
2        2018-01-01T06:28:39.    4.00       Mobile           New  
3        2018-01-01T06:18:16.    3.00       Mobile           New  
4        2018-01-01T11:54:20.    9.00       Mobile           New  
...                       ...     ...          ...           ...  
7740289      2019-01-01T02:48    1.00         Card           New  
7740290      2019-01-01T02:34    1.00         Card           New  
7740291      2019-01-01T02:27    1.00         Card           New  
7740292      2019-01-01T02:37    1.00         Card           New  
7740293      2019-01-01T02:06    0.25         Cash           New  

[7740294 rows x 9 columns]

In [116]:
#select only oakland zones
individual_oakland_records_2018 = individual_records_2018[individual_records_2018['zone'].str.contains('Oakland')]

#select columns we want and create datetime objects
individual_oakland_records_2018 = individual_oakland_records_2018[['zone', 'payment_start_utc', 'payment_end_utc', 'amount']]
individual_oakland_records_2018["payment_start_utc"] = pd.to_datetime(individual_oakland_records_2018["payment_start_utc"])
individual_oakland_records_2018["payment_end_utc"] = pd.to_datetime(individual_oakland_records_2018["payment_end_utc"])

#limit the startdate to the aggregates date
date_before = pd.Timestamp(2018, 7, 29) #hardcoded because of the last date from our 50,000 aggregates
individual_oakland_records_2018 = individual_oakland_records_2018[individual_oakland_records_2018['payment_start_utc'] <= date_before]

#modify the times to avoid this UTC bullshit ... only got 10% of the way through calculations before realizing everything was off by several hours
individual_oakland_records_2018['payment_start_utc'] = individual_oakland_records_2018['payment_start_utc'].dt.tz_localize('UTC')
individual_oakland_records_2018['payment_start_east'] = individual_oakland_records_2018['payment_start_utc'].dt.tz_convert('US/Eastern')
individual_oakland_records_2018['payment_end_utc'] = individual_oakland_records_2018['payment_end_utc'].dt.tz_localize('UTC')
individual_oakland_records_2018['payment_end_east'] = individual_oakland_records_2018['payment_end_utc'].dt.tz_convert('US/Eastern')


#determine the startbucket of a particular transaction, and sort
individual_oakland_records_2018['start_bucket'] = individual_oakland_records_2018["payment_start_east"].dt.floor('10min')
individual_oakland_records_2018 = individual_oakland_records_2018.sort_values(by='start_bucket')

individual_oakland_records_2018

zone         payment_start_utc           payment_end_utc  \
16       409 - Oakland 3 2018-01-01 12:58:00+00:00 2018-01-01 15:28:00+00:00   
30       407 - Oakland 1 2018-01-01 13:44:00+00:00 2018-01-01 15:44:00+00:00   
41       407 - Oakland 1 2018-01-01 13:44:00+00:00 2018-01-01 17:44:00+00:00   
77       410 - Oakland 4 2018-01-01 15:35:00+00:00 2018-01-01 16:35:00+00:00   
66       410 - Oakland 4 2018-01-01 15:53:00+00:00 2018-01-01 17:53:00+00:00   
...                  ...                       ...                       ...   
4517627  409 - Oakland 3 2018-07-28 21:53:00+00:00 2018-07-28 22:00:00+00:00   
4517322  409 - Oakland 3 2018-07-28 21:53:00+00:00 2018-07-28 21:59:00+00:00   
4518199  407 - Oakland 1 2018-07-28 21:51:00+00:00 2018-07-28 21:56:00+00:00   
4517476  408 - Oakland 2 2018-07-28 21:55:00+00:00 2018-07-28 22:00:00+00:00   
4517675  409 - Oakland 3 2018-07-28 21:55:00+00:00 2018-07-28 22:00:00+00:00   

         amount        payment_start_east          payment_end_east  \
16         7.50 2018-01-01 07:58:00-05:00 2018-01-01 10:28:00-05:00   
30         6.00 2018-01-01 08:44:00-05:00 2018-01-01 10:44:00-05:00   
41         6.00 2018-01-01 08:44:00-05:00 2018-01-01 12:44:00-05:00   
77         1.75 2018-01-01 10:35:00-05:00 2018-01-01 11:35:00-05:00   
66         3.00 2018-01-01 10:53:00-05:00 2018-01-01 12:53:00-05:00   
...         ...                       ...                       ...   
4517627    1.00 2018-07-28 17:53:00-04:00 2018-07-28 18:00:00-04:00   
4517322    0.30 2018-07-28 17:53:00-04:00 2018-07-28 17:59:00-04:00   
4518199    0.25 2018-07-28 17:51:00-04:00 2018-07-28 17:56:00-04:00   
4517476    0.25 2018-07-28 17:55:00-04:00 2018-07-28 18:00:00-04:00   
4517675    0.25 2018-07-28 17:55:00-04:00 2018-07-28 18:00:00-04:00   

                     start_bucket  
16      2018-01-01 07:50:00-05:00  
30      2018-01-01 08:40:00-05:00  
41      2018-01-01 08:40:00-05:00  
77      2018-01-01 10:30:00-05:00  
66      2018-01-01 10:50:00-05:00  
...                           ...  
4517627 2018-07-28 17:50:00-04:00  
4517322 2018-07-28 17:50:00-04:00  
4518199 2018-07-28 17:50:00-04:00  
4517476 2018-07-28 17:50:00-04:00  
4517675 2018-07-28 17:50:00-04:00  

[766231 rows x 7 columns]

In [118]:
oakland_aggregates_df

mobile_transactions                       end             zone  \
0                        1 2018-01-01 08:00:00-05:00  409 - Oakland 3   
12202                    2 2018-01-01 08:50:00-05:00  407 - Oakland 1   
24775                    1 2018-01-01 10:40:00-05:00  410 - Oakland 4   
12203                    1 2018-01-01 11:00:00-05:00  407 - Oakland 1   
24776                    2 2018-01-01 11:00:00-05:00  410 - Oakland 4   
...                    ...                       ...              ...   
12200                    5 2018-07-28 16:10:00-04:00  409 - Oakland 3   
37542                    3 2018-07-28 16:10:00-04:00  410 - Oakland 4   
24774                    1 2018-07-28 16:20:00-04:00  407 - Oakland 1   
49999                    2 2018-07-28 16:20:00-04:00  408 - Oakland 2   
12201                    0 2018-07-28 16:20:00-04:00  409 - Oakland 3   

       meter_transactions                     start  mobile_payments     _id  \
0                       0 2018-01-01 07:50:00-05:00             7.50      19   
12202                   0 2018-01-01 08:40:00-05:00            12.00      39   
24775                   0 2018-01-01 10:30:00-05:00             1.75      69   
12203                   0 2018-01-01 10:50:00-05:00             5.25      78   
24776                   0 2018-01-01 10:50:00-05:00             5.25      79   
...                   ...                       ...              ...     ...   
12200                   8 2018-07-28 16:00:00-04:00            18.10  479709   
37542                   6 2018-07-28 16:00:00-04:00             4.25  479710   
24774                  11 2018-07-28 16:10:00-04:00             4.50  479738   
49999                   7 2018-07-28 16:10:00-04:00             7.00  479739   
12201                   8 2018-07-28 16:10:00-04:00             0.00  479740   

       meter_payments rate total spaces free spaces  
0                0.00    3          476         476  
12202            0.00    3          227         227  
24775            0.00    3          572         572  
12203            0.00    3          227         227  
24776            0.00    3          572         572  
...               ...  ...          ...         ...  
12200           27.65    3          476         476  
37542           24.05    3          572         572  
24774           31.45    3          227         227  
49999           19.60    3          301         301  
12201           14.90    3          476         476  

[50000 rows x 11 columns]

In [119]:
aggs_start_bucket_index = 0

for index, transaction in individual_oakland_records_2018.iterrows():
    
    trans_start_bucket_time = transaction['start_bucket']
    trans_end_time = transaction['payment_end_east']
    trans_zone = transaction['zone']
    
    #ADD SOMETHING HERE TO PREVENT FALLING OFF THE BACK
    
    while(oakland_aggregates_df.iloc[aggs_start_bucket_index]['start'] < trans_start_bucket_time):
        bucket_start = oakland_aggregates_df.iloc[aggs_start_bucket_index]['start']
        bucket_zone = oakland_aggregates_df.iloc[aggs_start_bucket_index]['zone']
        total_spaces = oakland_aggregates_df.iloc[aggs_start_bucket_index]['total spaces']
        available_spaces = oakland_aggregates_df.iloc[aggs_start_bucket_index]['free spaces']
        
        print("Bucket", aggs_start_bucket_index, " | Zone ", bucket_zone, "; Start time: ", bucket_start, "; Total spaces: ", total_spaces, "; Available spaces: ", available_spaces)
        aggs_start_bucket_index += 1;
            
    i = aggs_start_bucket_index
    while(oakland_aggregates_df.iloc[i]['start'] < trans_end_time):
        #use .iloc because it uses indices... kind of ugly but oh well.  10 is the index for 'free spaces'
        if(oakland_aggregates_df.iloc[i]['zone'] == trans_zone):
            oakland_aggregates_df.iloc[i,10] = int(oakland_aggregates_df.iloc[i, 10]) - 1 
        i += 1
        #ADD SOMETHING HERE TOO

Bucket 0  | Zone  409 - Oakland 3 ; Start time:  2018-01-01 07:50:00-05:00 ; Total spaces:  476 ; Available spaces:  475
Bucket 1  | Zone  407 - Oakland 1 ; Start time:  2018-01-01 08:40:00-05:00 ; Total spaces:  227 ; Available spaces:  225
Bucket 2  | Zone  410 - Oakland 4 ; Start time:  2018-01-01 10:30:00-05:00 ; Total spaces:  572 ; Available spaces:  571
Bucket 3  | Zone  407 - Oakland 1 ; Start time:  2018-01-01 10:50:00-05:00 ; Total spaces:  227 ; Available spaces:  225
Bucket 4  | Zone  410 - Oakland 4 ; Start time:  2018-01-01 10:50:00-05:00 ; Total spaces:  572 ; Available spaces:  569
Bucket 5  | Zone  408 - Oakland 2 ; Start time:  2018-01-01 11:00:00-05:00 ; Total spaces:  301 ; Available spaces:  300
Bucket 6  | Zone  408 - Oakland 2 ; Start time:  2018-01-01 11:10:00-05:00 ; Total spaces:  301 ; Available spaces:  298
Bucket 7  | Zone  408 - Oakland 2 ; Start time:  2018-01-01 11:40:00-05:00 ; Total spaces:  301 ; Available spaces:  297
Bucket 8  | Zone  407 - Oakland 

Bucket 68  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 07:50:00-05:00 ; Total spaces:  227 ; Available spaces:  198
Bucket 69  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 07:50:00-05:00 ; Total spaces:  301 ; Available spaces:  289
Bucket 70  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 07:50:00-05:00 ; Total spaces:  476 ; Available spaces:  466
Bucket 71  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 07:50:00-05:00 ; Total spaces:  572 ; Available spaces:  556
Bucket 72  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 08:00:00-05:00 ; Total spaces:  227 ; Available spaces:  158
Bucket 73  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 08:00:00-05:00 ; Total spaces:  301 ; Available spaces:  277
Bucket 74  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 08:00:00-05:00 ; Total spaces:  476 ; Available spaces:  441
Bucket 75  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 08:00:00-05:00 ; Total spaces:  572 ; Available spaces:  510
Bucket 76  | Zone  407 -

Bucket 136  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 10:40:00-05:00 ; Total spaces:  227 ; Available spaces:  76
Bucket 137  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 10:40:00-05:00 ; Total spaces:  301 ; Available spaces:  217
Bucket 138  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 10:40:00-05:00 ; Total spaces:  476 ; Available spaces:  352
Bucket 139  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 10:40:00-05:00 ; Total spaces:  572 ; Available spaces:  439
Bucket 140  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 10:50:00-05:00 ; Total spaces:  227 ; Available spaces:  69
Bucket 141  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 10:50:00-05:00 ; Total spaces:  301 ; Available spaces:  217
Bucket 142  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 10:50:00-05:00 ; Total spaces:  476 ; Available spaces:  339
Bucket 143  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 10:50:00-05:00 ; Total spaces:  572 ; Available spaces:  437
Bucket 144  | Zone

Bucket 204  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 13:30:00-05:00 ; Total spaces:  227 ; Available spaces:  78
Bucket 205  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 13:30:00-05:00 ; Total spaces:  301 ; Available spaces:  187
Bucket 206  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 13:30:00-05:00 ; Total spaces:  476 ; Available spaces:  285
Bucket 207  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 13:30:00-05:00 ; Total spaces:  572 ; Available spaces:  396
Bucket 208  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 13:40:00-05:00 ; Total spaces:  227 ; Available spaces:  73
Bucket 209  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 13:40:00-05:00 ; Total spaces:  301 ; Available spaces:  187
Bucket 210  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 13:40:00-05:00 ; Total spaces:  476 ; Available spaces:  281
Bucket 211  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 13:40:00-05:00 ; Total spaces:  572 ; Available spaces:  400
Bucket 212  | Zone

Bucket 272  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 16:20:00-05:00 ; Total spaces:  227 ; Available spaces:  137
Bucket 273  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 16:20:00-05:00 ; Total spaces:  301 ; Available spaces:  229
Bucket 274  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 16:20:00-05:00 ; Total spaces:  476 ; Available spaces:  358
Bucket 275  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 16:20:00-05:00 ; Total spaces:  572 ; Available spaces:  463
Bucket 276  | Zone  407 - Oakland 1 ; Start time:  2018-01-02 16:30:00-05:00 ; Total spaces:  227 ; Available spaces:  141
Bucket 277  | Zone  408 - Oakland 2 ; Start time:  2018-01-02 16:30:00-05:00 ; Total spaces:  301 ; Available spaces:  234
Bucket 278  | Zone  409 - Oakland 3 ; Start time:  2018-01-02 16:30:00-05:00 ; Total spaces:  476 ; Available spaces:  357
Bucket 279  | Zone  410 - Oakland 4 ; Start time:  2018-01-02 16:30:00-05:00 ; Total spaces:  572 ; Available spaces:  471
Bucket 280  | Zo

...

Bucket 49517  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 07:50:00-04:00 ; Total spaces:  227 ; Available spaces:  205
Bucket 49518  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 07:50:00-04:00 ; Total spaces:  301 ; Available spaces:  254
Bucket 49519  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 07:50:00-04:00 ; Total spaces:  476 ; Available spaces:  453
Bucket 49520  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 07:50:00-04:00 ; Total spaces:  572 ; Available spaces:  529
Bucket 49521  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 08:00:00-04:00 ; Total spaces:  227 ; Available spaces:  159
Bucket 49522  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 08:00:00-04:00 ; Total spaces:  301 ; Available spaces:  182
Bucket 49523  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 08:00:00-04:00 ; Total spaces:  476 ; Available spaces:  402
Bucket 49524  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 08:00:00-04:00 ; Total spaces:  572 ; Available spaces:  464


Bucket 49585  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 10:40:00-04:00 ; Total spaces:  227 ; Available spaces:  -8
Bucket 49586  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 10:40:00-04:00 ; Total spaces:  301 ; Available spaces:  23
Bucket 49587  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 10:40:00-04:00 ; Total spaces:  476 ; Available spaces:  219
Bucket 49588  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 10:40:00-04:00 ; Total spaces:  572 ; Available spaces:  241
Bucket 49589  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 10:50:00-04:00 ; Total spaces:  227 ; Available spaces:  -5
Bucket 49590  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 10:50:00-04:00 ; Total spaces:  301 ; Available spaces:  19
Bucket 49591  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 10:50:00-04:00 ; Total spaces:  476 ; Available spaces:  204
Bucket 49592  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 10:50:00-04:00 ; Total spaces:  572 ; Available spaces:  223
Buck

Bucket 49653  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 13:30:00-04:00 ; Total spaces:  227 ; Available spaces:  14
Bucket 49654  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 13:30:00-04:00 ; Total spaces:  301 ; Available spaces:  -3
Bucket 49655  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 13:30:00-04:00 ; Total spaces:  476 ; Available spaces:  151
Bucket 49656  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 13:30:00-04:00 ; Total spaces:  572 ; Available spaces:  227
Bucket 49657  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 13:40:00-04:00 ; Total spaces:  227 ; Available spaces:  7
Bucket 49658  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 13:40:00-04:00 ; Total spaces:  301 ; Available spaces:  12
Bucket 49659  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 13:40:00-04:00 ; Total spaces:  476 ; Available spaces:  153
Bucket 49660  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 13:40:00-04:00 ; Total spaces:  572 ; Available spaces:  234
Bucke

Bucket 49721  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 16:20:00-04:00 ; Total spaces:  227 ; Available spaces:  110
Bucket 49722  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 16:20:00-04:00 ; Total spaces:  301 ; Available spaces:  148
Bucket 49723  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 16:20:00-04:00 ; Total spaces:  476 ; Available spaces:  301
Bucket 49724  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 16:20:00-04:00 ; Total spaces:  572 ; Available spaces:  355
Bucket 49725  | Zone  407 - Oakland 1 ; Start time:  2018-07-27 16:30:00-04:00 ; Total spaces:  227 ; Available spaces:  118
Bucket 49726  | Zone  408 - Oakland 2 ; Start time:  2018-07-27 16:30:00-04:00 ; Total spaces:  301 ; Available spaces:  152
Bucket 49727  | Zone  409 - Oakland 3 ; Start time:  2018-07-27 16:30:00-04:00 ; Total spaces:  476 ; Available spaces:  298
Bucket 49728  | Zone  410 - Oakland 4 ; Start time:  2018-07-27 16:30:00-04:00 ; Total spaces:  572 ; Available spaces:  385


IndexError: single positional indexer is out-of-bounds

In [148]:
#so there was a bug in the above code where i forgot to prevent the buckets from falling off of the end soooooo.....
#.... we have to use slighltly less than 50,000 datapoints LOL
final_df = oakland_aggregates_df.iloc[0:49769] 
final_df

mobile_transactions                       end             zone  \
0                        1 2018-01-01 08:00:00-05:00  409 - Oakland 3   
12202                    2 2018-01-01 08:50:00-05:00  407 - Oakland 1   
24775                    1 2018-01-01 10:40:00-05:00  410 - Oakland 4   
12203                    1 2018-01-01 11:00:00-05:00  407 - Oakland 1   
24776                    2 2018-01-01 11:00:00-05:00  410 - Oakland 4   
...                    ...                       ...              ...   
24716                    0 2018-07-28 06:10:00-04:00  407 - Oakland 1   
49939                    1 2018-07-28 06:10:00-04:00  408 - Oakland 2   
37484                    2 2018-07-28 06:10:00-04:00  410 - Oakland 4   
24717                    2 2018-07-28 06:20:00-04:00  407 - Oakland 1   
49940                    0 2018-07-28 06:20:00-04:00  408 - Oakland 2   

       meter_transactions                     start  mobile_payments     _id  \
0                       0 2018-01-01 07:50:00-05:00             7.50      19   
12202                   0 2018-01-01 08:40:00-05:00            12.00      39   
24775                   0 2018-01-01 10:30:00-05:00             1.75      69   
12203                   0 2018-01-01 10:50:00-05:00             5.25      78   
24776                   0 2018-01-01 10:50:00-05:00             5.25      79   
...                   ...                       ...              ...     ...   
24716                   2 2018-07-28 06:00:00-04:00             0.00  477788   
49939                   3 2018-07-28 06:00:00-04:00             3.25  477789   
37484                   0 2018-07-28 06:00:00-04:00            23.75  477790   
24717                   1 2018-07-28 06:10:00-04:00            24.25  477793   
49940                   3 2018-07-28 06:10:00-04:00             0.00  477794   

       meter_payments rate total spaces free spaces  
0                0.00    3          476         475  
12202            0.00    3          227         225  
24775            0.00    3          572         571  
12203            0.00    3          227         225  
24776            0.00    3          572         569  
...               ...  ...          ...         ...  
24716           16.00    3          227         227  
49939           10.25    3          301         297  
37484            0.00    3          572         570  
24717            5.00    3          227         225  
49940           41.50    3          301         297  

[49769 rows x 11 columns]

In [8]:
#make a couple more adjustments to the final_df

#add the name of the day of the week
final_df['day_of_week'] = final_df['start'].dt.day_name()

#separate the time into its own column
final_df['time'] = final_df['start'].dt.time

#separate the date (no year) into its own column
final_df['date'] = final_df['start'].dt.strftime('%m-%d')

#occupancy is a ratio of free spaces to total spaces, produces a warning that pisses me off, but it works....this time
final_df['occupancy'] = final_df['free spaces'].astype(int) / final_df['total spaces'].astype(int) 

#round occupancy to 3 and make sure its not negative
final_df['occupancy'] = final_df['occupancy'].round(3)
temp = final_df['occupancy']
temp[temp < 0] = 0
final_df['occupancy'] = temp #this temp stuff is ugly but pandas syntax is uglier

#and finally, we will only use the inputs/output that we want for the AutoML process
final_df = final_df[['start', 'end', 'zone', 'day_of_week', 'date', 'time', 'occupancy']]

final_df

ValueError: Tz-aware datetime.datetime cannot be converted to datetime64 unless utc=True

In [153]:
# export final_df to a .csv file
final_df.to_csv("oakland_true_occupancy.csv")

# also save oakland_aggregates_df.iloc[0:49769] because that took way too long to calculate
backup_df = oakland_aggregates_df.iloc[0:49769]
backup_df.to_csv("oakland_free_spaces.csv")